## Chiller Flow Calculations

This notebook calculates the flow requirements and flow capacity of cooling the ETL disc section with our chiller.


#### Links

  - Our Chiller: [link](https://www.julabo.com/en-us/products/refrigerated-circulators/refrigerated-heating-circulators/dyneo-dd-1000f)
  - Antifreeze properties: [link](https://www.engineeringtoolbox.com/ethylene-glycol-d_146.html)
   

### Cooling Requirements

Each full module is estimated to produce 4.53 W of heat. The service hybrid is estimated at 18 W. A half-populated (ie only one side) disc section has 12 modules and 1 service hybrid producing a total of **72.36 Watts** of heat. A fully populated section would have 6 additional modules and 2 additional service hybrids producing 45.18 additional watts of heat. This document will work under the assumption of a half-populated disc section.

The chiller is operating with a 50/50 mix of water and propylene glycol. The physical properties of interest are:

  - density: 1.1 g/ml @ -25 $^{\circ}$C
  - specific heat: ~0.8 J/(g$\cdot^{\circ}$C)
  - freezing point: -36.8 $^{\circ}$C

From this information, we can calculate the flow rate needed, assuming a specific input and output temperatures of the cooling fluid.

In [5]:
# Assume highest possible delta-t 
t1 = -36.8  # Celcius
t2 = -20  # Celcius

dt = t2 - t1
rho = (0.8 * dt) / 1.1  # heat removed per ml

flow_rate = 72.36 / rho
print(f"flow rate: {flow_rate*60/1000} L/min")

flow rate: 0.3553392857142858 L/min


### Flow-rate potential

The flow rate of a liquid through a pipe can be estimated by applying a variant ([ref](http://kb.eng-software.com/eskb/ask-an-engineer/theory-equations-and-calculated-results-questions/relationship-between-pressure-drop-and-flow-rate-in-a-pipeline)) of the Bernoulli equation:

$$
(P_1 - P_2) = \rho g \left[(Z_2 - Z_1) + \left(\frac{v_2^2 - v_1^2}{2g}\right) + H_L\right]
$$

Where,

  - $\rho$ - fluid density (kg/m$^3$)
  - $g$ - accelleration due to gravity (m/s$^2$)
  - $v_{1,2}$ - velocity at two points in pipe (m/s)
  - $Z_{1,2}$ - elevations at two points in pipe (m)
  - $H_L$ - Head loss, aka energy loss due to friction, vibrations, etc between two points (m)

For flow through a constant-diameter pipe, the fluid velocities $v_1$ and $v_2$ are equal. Furthermore, if the pipe is horizontal, the two elevations, $Z_1$ and $Z_2$ are also equal. This simplifies the equation to:

$$
(P_1 - P_2) = \rho g H_L
$$

This means that the pressure difference between the ends of the pipe is caused solely by the *head loss*. The head loss can be calculated using the Darcy-Weisbach equation:

$$
H_L = f \frac{L}{D} \frac{v^2}{2g}
$$

Where,

  - $f$ - Darcy friction factor (dimensionless)
  - $L$ - Pipe length (m)
  - $D$ - Inside pipe diameter (m)
  - $v$ - fluid velocity (m/s)

Calculating the *Darcy friction factor* first requires calculating the Reynold's number of the fluid. For this calculation, we will assume that the antifreeze mixture is water-like.

The Reynolds number is defined as:

$$
\mathrm{Re} = \frac{\rho u L}{\mu}
$$

Where,

  - $\rho$ - fluid density (999.7 kg/m$^3$)
  - $u$ - flow speed through pipe (currently unknown but guess 1 m/s - this can be iterated if needed)
  - $\mu$ - dynamic viscosity (1.308E-3 kg/m$\cdot$s)
  - $L$ - characteristic linear dimension, diameter of pipe in this case (3E-3 m)
  
Putting in numbers, we get a Reynolds number of 2,293.

There are many methods to calculating the *darcy friction factor*, some more complicated than others. Let's use the fairly simple [*Halland equation*](https://en.wikipedia.org/wiki/Darcy_friction_factor_formulae#Approximations_of_the_Colebrook_equation) (which may or may not actually be applicable in this situation, see article).

$$
\frac{1}{\sqrt{f}} = -1.8 \log\left[\left(\frac{\epsilon/D}{3.7}\right)^{1.11} + \frac{6.9}{\mathrm{Re}}\right]
$$

The values $D$ and $\epsilon$ are the pipe's diameter and "effective roughness height", respectively. For these calculations, we will take $D=3$ mm and $\epsilon=100$ microns. Putting in numbers we get, $\frac{1}{\sqrt{f}}=3.3738$, or $f=7.15
E-2$.

Now that we have the *darcy friction factor*, let's rewrite the *head loss* equation to solve for the fluid velocity.

$$
v^2 = \frac{2g D}{L f} H_L
$$

Our pump is rated to supply a pressure of up to 10.2 psi, or 70.33 kPa. Let's assume that the low pressure end of the pipe is at atmospheric pressure, meaning that $\rho g H_L = 70.33 \mathrm{kPa}$, giving $H_L=7.17E-3$ m.

One last bit of information we need is the length of the pipe. Let's use $L=1$ m. Now we have everything we need to calculate the fluid velocity. Putting in numbers yields: $v=0.24$ m/s. Although this is about 25% of our initial velocity estimate, let's push on to the final number. The flow rate is $F=v\pi\left(\frac{D}{2}\right)^2=1.71E-6$ m$^3$/s, or **0.103 L/min**. This is about 1/3 of what is needed to chill a half-populated disc section.